In [1]:
from datasets import load_dataset, DatasetDict, Dataset
import os
import re
from pydub import AudioSegment
import pandas as pd

import pylab as plt

ds = load_dataset("aaparajit02/punjabi-asr", num_proc=2, cache_dir="punjabi-asr_DS")
print(ds)

Resolving data files:   0%|          | 0/22 [00:00<?, ?it/s]

Loading dataset shards:   0%|          | 0/22 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['audio', 'transcript', 'english'],
        num_rows: 39238
    })
})


In [2]:
ds['train'][0]

{'audio': {'path': 'punjabi_0.wav',
  'array': array([ 0.17160034,  0.04043579, -0.0741272 , ...,  0.08728027,
          0.09371948,  0.11239624]),
  'sampling_rate': 16000},
 'transcript': 'ਉਨ੍ਹਾਂ ਕਿਹਾ ਕਿ ਦੇਸ਼ ਦੇ ਤੇਜ਼ੀ ਨਾਲ ਵਿਕਾਸ ਵਿਚ ਨੌਜੁਆਨਾਂ ਦਾ ਬਹੁਤ ਵੱਡ ਯੋਗਦਾਨ ਏ',
 'english': "He said that the contribution of the youth in the country's development is immense."}

In [3]:
ds = ds.remove_columns('english')
ds = ds.rename_column('transcript', 'text')


In [4]:

def get_duration(x):
    x['gender'] = None
    x['speaker_id'] = None

    x['duration'] = len(x['audio']['array']) / x['audio']['sampling_rate']
    return x

res = []
ds = ds['train']


In [5]:
for i in range(16):
    shard = ds.shard( 16, i, contiguous=True)
    res.append(shard.map(get_duration, num_proc=16, cache_file_name= f'/mnt/sea/tmp/map{i}.cache'))


from datasets import concatenate_datasets
ds_res = concatenate_datasets(res)
ds_res

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

...

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/2452 [00:00<?, ? examples/s]

Dataset({
    features: ['audio', 'text', 'gender', 'speaker_id', 'duration'],
    num_rows: 53950
})

In [6]:
ds = DatasetDict({'train': ds_res})
ds

DatasetDict({
    train: Dataset({
        features: ['audio', 'text', 'gender', 'speaker_id', 'duration'],
        num_rows: 53950
    })
})

In [7]:
ds_res[0]

{'audio': {'path': None,
  'array': array([ 0.17160034,  0.04043579, -0.0741272 , ...,  0.08728027,
          0.09371948,  0.11239624]),
  'sampling_rate': 16000},
 'text': 'ਉਨ੍ਹਾਂ ਕਿਹਾ ਕਿ ਦੇਸ਼ ਦੇ ਤੇਜ਼ੀ ਨਾਲ ਵਿਕਾਸ ਵਿਚ ਨੌਜੁਆਨਾਂ ਦਾ ਬਹੁਤ ਵੱਡ ਯੋਗਦਾਨ ਏ',
 'gender': None,
 'speaker_id': None,
 'duration': 5.06}

In [ ]:
from datasets import Audio
ds['train'] = ds['train'].cast_column("audio", Audio(sampling_rate=16000))
ds

In [7]:
ds.save_to_disk('/mnt/data/Speech Dataset/processed_datasets/shrutilipi_pa_ASR', num_proc=24)

Saving the dataset (0/31 shards):   0%|          | 0/53950 [00:00<?, ? examples/s]

In [1]:
from datasets import load_from_disk

ds = load_from_disk('/mnt/data/Speech Dataset/processed_datasets/shrutilipi_pa_ASR')
ds

Loading dataset from disk:   0%|          | 0/31 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['audio', 'text', 'gender', 'speaker_id', 'duration'],
        num_rows: 53950
    })
})

In [3]:
import IPython.display as ipd
from IPython.display import Audio

durations = ds['train']['duration']
# get indexes of 20 longest audio files
indexes = sorted(range(len(durations)), key=lambda x: durations[x], reverse=True)[:20]
text = ds['train']['text']
indexes = sorted(range(len(text)), key=lambda x: len(text[x]), reverse=True)[:20]
print(indexes)

indexes = list(range(20))
ds_check = ds['train'].select(indexes)

def display_audio(row):
    print(row['text'])
    return Audio(row['audio']['array'], rate=16000, autoplay=True)
# sort by length of text
for i in range(20):
    r = display_audio(ds_check[i])
    ipd.display(r)

[11559, 49153, 46249, 16183, 30895, 2229, 3475, 24907, 39619, 15298, 30010, 659, 52826, 16144, 30856, 10314, 16925, 31637, 46125, 22968]
ਉਨ੍ਹਾਂ ਕਿਹਾ ਕਿ ਦੇਸ਼ ਦੇ ਤੇਜ਼ੀ ਨਾਲ ਵਿਕਾਸ ਵਿਚ ਨੌਜੁਆਨਾਂ ਦਾ ਬਹੁਤ ਵੱਡ ਯੋਗਦਾਨ ਏ


ਉਪ ਰਾਸ਼ਟਰਪਤੀ ਐਮ ਵੈਂਕਈਆ ਨਾਇਡੂ ਨੇ ਸਾਰੇ ਵਿਦਿਅਕ ਅਦਾਰਿਆਂ ਨੂੰ ਸੱਦਾ ਦਿੱਤੈ ਕਿ ਉਹ ਵਿਦਿਆਰਥੀਆਂ ਨੂੰ ਮਿਆਰੀ ਘੱਟ ਖਰਚੀਲੀ ਅਤੇ ਸਾਰਥਿਕ ਸਿਖਿਆ ਮੁਹੱਈਆ ਕਰਾਉਣ ਲਈ ਸੈਂਟਰ ਆਫ ਐਕਸੀਲੈਂਸ ਵਜੋਂ ਕੰਮ ਕਰਨ


ਵਿਨੋਦ ਖੰਨਾ ਇਸ ਸੀਟ ਤੋਂ 4 ਵਾਰ ਜੇਤੂ ਰਹੇ ਸਨ ਜਦਕਿ 2009 ਵਿਚ ਇਕ ਵਾਰ ਹਾਰ ਗਏ ਸਨ


ਸ੍ਰੀ ਦਾਸ ਨੇ ਕਿਹਾ ਕਿ ਪਿਛਲੀ ਦਸੰਬਰ ਚ ਲਖਨਾਊ ਚ ਹੋਏ ਸਮਾਗਮ ਚ ਇਹ ਫੈਸਲਾ ਲਿਆ ਗਿਆ ਸੀ ਕਿ ਵੱਖ ਵੱਖ ਸ਼ਹਿਰਾਂ ਚ ਅਜਿਹੇ ਮਸ਼ਵਰਾ ਸੰਮੇਲਨ ਕੀਤੇ ਜਾਣਗੇ


ਆਈ ਆਈ ਟੀ ਰੋਪੜ ਨੇ ਉਵਰ ਆਲ ਟਾਈਮਜ਼ ਹਾਇਰ ਐਜੂਕੇਸ਼ਨ ਵਰਲਡ ਰੈਕਿੰਗ ਦੇ ਨਾਲ ਨਾਲ ਏਸ਼ੀਆ ਯੂਨੀਵਰਸਿਟੀ ਰੈਕਿੰਗ 2020 ਚ 47ਵਾਂ ਰੈਂਕ ਹਾਸਲ ਕੀਤੈ


...

ਇਹ ਵੀ ਦਸਿਆ ਗਿਐ ਕਿ ਤਾਂਬੇ ਦੇ ਬਰਤਨ ਕਈ ਔਸ਼ਧੀ ਗੁਣਾਂ ਨਾਲ ਭਰਪੂਰ ਹੁੰਦੇ ਨੇ ਅਤੇ ਇਨ੍ਹਾਂ ਚ ਕੋਈ ਵੀ ਬੈਕਟੀਰਿਆ ਨਹੀਂ ਰਹਿ ਸਕਦਾ


ਯੋਗਤਾ ਤਹਿਤ ਇਹ ਲਾਜ਼ਮੀ ਹੋਵੇਗਾ ਕਿ ਪੱਤਰਕਾਰ ਖਿਲਾਫ ਕੋਈ ਅਪਰਾਧਿਕ ਕੇਸ ਨਾ ਚਲਦਾ ਹੋਵੇ ਅਤੇ ਨਾ ਹੀ ਕਿਸੇ ਵੀ ਸਰਕਾਰੀ ਜਾਇਦਾਦ ਤੇ ਉਸ ਦਾ ਗੈਰਕਾਨੂੰਨੀ ਕਬਜ਼ਾ ਹੋਵੇ ਅਤੇ ਪੱਤਰਕਾਰ ਵੱਲੋਂ ਪੂਰਨ ਜਾਂ ਅੰਸ਼ ਰੂਪ ਵਾਲੇ ਕਿਸੇ ਫੰਡ ਤੋਂ ਮਿਲਦੀ ਪੈਨਸ਼ਨ ਤੋਂ ਇਲਾਵਾ ਹੋਰ ਕੋਈ ਤਨਖਾਹ ਜਾਂ ਪੈਨਸ਼ਨ ਨਾ ਲਈ ਜਾ ਰਹੀ ਹੋਵੇ


ਗੈਂਗਸਟਰ ਦੀ ਬਾਅਦ ਚ ਮੌਤ ਹੋ ਗਈ


ਇਸ ਮੁਕਾਬਲੇ ਚ ਗੈਂਗਸਟਰ ਅੰਕਿਤ ਭਾਦੂ ਜ਼ਖ਼ਮੀ ਹੋ ਗਿਆ


ਮਨੁੱਖੀ ਵਸੀਲਿਆਂ ਦੇ ਵਿਕਾਸ ਬਾਰੇ ਕੇਂਦਰੀ ਮੰਤਰੀ ਪ੍ਰਕਾਸ਼ ਜਾਵੜੇਕਰ ਨੇ ਅੱਜ ਰਾਜ ਸਭਾ ਚ ਇਕ ਬਿਆਨ ਵਿਚ ਕਿਹਾ ਕਿ ਜੇ ਸਰਕਾਰ ਵੱਲੋਂ ਅਦਾਲਤ ਵਿਚ ਦਾਇਰ ਨਜ਼ਰਸਾਨੀ ਪਟੀਸ਼ਨ ਰੱਦ ਹੁੰਦੀ ਏ ਤਾਂ ਇਹ ਆਰਡੀਨੈਂਸ ਲਿਆ ਜਾਏਗਾ
